In [1]:
import ray
ray.init()

2024-02-15 18:10:11,930	INFO worker.py:1715 -- Started a local Ray instance. View the dashboard at http://127.0.0.1:8266 


RayContext(dashboard_url='127.0.0.1:8266', python_version='3.11.7', ray_version='2.9.2', ray_commit='fce7a361807580953364e2da964f9498f3123bf9', protocol_version=None)

In [2]:
import numpy as np

In [3]:
cells = [
    [4, 5, 0, 0, 0, 0, 0, 0, 0],
    [0, 0, 2, 0, 7, 0, 6, 3, 0],
    [0, 0, 0, 0, 0, 0, 0, 2, 8],
    [0, 0, 0, 9, 5, 0, 0, 0, 0],
    [0, 8, 6, 0, 0, 0, 2, 0, 0],
    [0, 2, 0, 6, 0, 0, 7, 5, 0],
    [0, 0, 0, 0, 0, 0, 4, 7, 6],
    [0, 7, 0, 0, 4, 5, 0, 0, 0],
    [0, 0, 8, 0, 0, 9, 0, 0, 0]
]
np_cells=np.array(cells)

Debug

In [23]:
np_cells[:,:]

array([[4, 5, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 2, 0, 7, 0, 6, 3, 0],
       [0, 0, 0, 0, 0, 0, 0, 2, 8],
       [0, 0, 0, 9, 5, 0, 0, 0, 0],
       [0, 8, 6, 0, 0, 0, 2, 0, 0],
       [0, 2, 0, 6, 0, 0, 7, 5, 0],
       [0, 0, 0, 0, 0, 0, 4, 7, 6],
       [0, 7, 0, 0, 4, 5, 0, 0, 0],
       [0, 0, 8, 0, 0, 9, 0, 0, 0]])

In [4]:
print(np_cells.shape)
arr_3x3x3x3 = np_cells.reshape(3, 3, 3, 3)
arr_3x3x3x3_transposed = arr_3x3x3x3.transpose(0, 2, 1, 3)
print(arr_3x3x3x3_transposed.shape)
print(type(arr_3x3x3x3_transposed[0,0]))
arr_3x3x3x3_transposed[0,0].reshape(9,1)


(9, 9)
(3, 3, 3, 3)
<class 'numpy.ndarray'>


array([[4],
       [5],
       [0],
       [0],
       [0],
       [2],
       [0],
       [0],
       [0]])

Single Process

In [31]:
def getBlocksS():
    # Reshape to a 3x3x3x3 array
    arr_3x3x3x3 = np_cells.reshape(3, 3, 3, 3)

    # Transpose the axes to rearrange dimensions
    arr_3x3x3x3_transposed = arr_3x3x3x3.transpose(0, 2, 1, 3)
  
    # Extract each 3x3 subarray
    # subarrays_3x3 = arr_3x3x3x3_transposed.reshape(9, 3, 3)
    return arr_3x3x3x3_transposed

def getBlock(row, col):
    return blocks[row, col].reshape(9)
def getRow(row):
    return np_cells[row]

def getCol(col):
    return np_cells[:, col]

blocks=getBlocksS()
getBlock(0,1)

array([0, 0, 0, 0, 7, 0, 0, 0, 0])

In [46]:
class Cell:
    def __init__(self, initial_value, row_index, col_index):
        """
        Initializes a cell with the given initial value.
        """
        self._value = initial_value
        self.row_index=row_index
        self.col_index=col_index
        self.row=getRow(row_index)
        self.col=getCol(col_index)
        self.block=getBlock(row_index // 3, col_index // 3)
        self.possibilities={i+1 for i in range(9)}

    def calculate(self):
        """
        Performs a calculation on the cell value based on the given operation and operand.
        Supported operations: '+', '-', '*', '/'.
        """
        for i in self.row:
            if i in self.possibilities:
                self.possibilities.remove(i)
        for j in self.col:
            if j in self.possibilities:
                self.possibilities.remove(j)
        for k in self.block:
            if k in self.possibilities:
                self.possibilities.remove(k)
                
    

In [43]:
0//3
2//3

0

In [47]:
x=Cell(0, 0, 2)
x.calculate()
print("row:",x.row)
print("col:",x.col)
print("block:", x.block)
x.possibilities

row: [4 5 0 0 0 0 0 0 0]
col: [0 2 0 0 6 0 0 0 8]
block: [4 5 0 0 0 2 0 0 0]


{1, 3, 7, 9}

multiple process

In [ ]:
@ray.remote
class CellP:

    def calculate(self, row_index, col_index):
        self._value = initial_value
        self.row_index=row_index
        self.col_index=col_index
        self.row=getRow(row_index)
        self.col=getCol(col_index)
        self.block=getBlock(row_index // 3, col_index // 3)
        self.possibilities={i+1 for i in range(9)}
        for i in self.row:
            if i in self.possibilities:
                self.possibilities.remove(i)
        for j in self.col:
            if j in self.possibilities:
                self.possibilities.remove(j)
        for k in self.block:
            if k in self.possibilities:
                self.possibilities.remove(k)

In [19]:
x=CellP(0, 0, 2)
x.calculate.remote()
print("row:",x.row)
print("col:",x.col)
print("block:", x.block)
x.possibilities


[[0 0 8 0 0 0 6 0 0]
 [0 3 2 0 0 5 7 0 0]
 [0 6 0 0 2 7 4 0 0]
 [0 0 0 0 0 0 0 5 9]
 [0 7 0 5 0 0 0 4 0]
 [0 0 0 9 0 6 0 0 0]
 [0 2 0 0 6 0 0 0 8]
 [5 0 0 0 8 2 0 7 0]
 [4 0 0 0 0 0 0 0 0]]


In [25]:
@ray.remote
def getCols():
    return np_cells[:]

@ray.remote
def getBlocks():
    # Reshape to a 3x3x3x3 array
    arr_3x3x3x3 = np_cells.reshape(3, 3, 3, 3)

    # Transpose the axes to rearrange dimensions
    arr_3x3x3x3_transposed = arr_3x3x3x3.transpose(0, 2, 1, 3)
  
    # Extract each 3x3 subarray
    # subarrays_3x3 = arr_3x3x3x3_transposed.reshape(9, 3, 3)
    return arr_3x3x3x3_transposed
@ray.remote
def getRows():
    rotate_array = np.rot90(np_cells)
    
    return rotate_array[:]


In [28]:
%%timeit
rows_h=getRows.remote()
cols_h=getCols.remote()
blocks_h=getBlocks.remote()
rows_p=ray.get(rows_h)
cols_p=ray.get(cols_h)
blocks_p=ray.get(blocks_h)
print(blocks_p)


[[[[4 5 0]
   [0 0 2]
   [0 0 0]]

  [[0 0 0]
   [0 7 0]
   [0 0 0]]

  [[0 0 0]
   [6 3 0]
   [0 2 8]]]


 [[[0 0 0]
   [0 8 6]
   [0 2 0]]

  [[9 5 0]
   [0 0 0]
   [6 0 0]]

  [[0 0 0]
   [2 0 0]
   [7 5 0]]]


 [[[0 0 0]
   [0 7 0]
   [0 0 8]]

  [[0 0 0]
   [0 4 5]
   [0 0 9]]

  [[4 7 6]
   [0 0 0]
   [0 0 0]]]]
[[[[4 5 0]
   [0 0 2]
   [0 0 0]]

  [[0 0 0]
   [0 7 0]
   [0 0 0]]

  [[0 0 0]
   [6 3 0]
   [0 2 8]]]


 [[[0 0 0]
   [0 8 6]
   [0 2 0]]

  [[9 5 0]
   [0 0 0]
   [6 0 0]]

  [[0 0 0]
   [2 0 0]
   [7 5 0]]]


 [[[0 0 0]
   [0 7 0]
   [0 0 8]]

  [[0 0 0]
   [0 4 5]
   [0 0 9]]

  [[4 7 6]
   [0 0 0]
   [0 0 0]]]]
[[[[4 5 0]
   [0 0 2]
   [0 0 0]]

  [[0 0 0]
   [0 7 0]
   [0 0 0]]

  [[0 0 0]
   [6 3 0]
   [0 2 8]]]


 [[[0 0 0]
   [0 8 6]
   [0 2 0]]

  [[9 5 0]
   [0 0 0]
   [6 0 0]]

  [[0 0 0]
   [2 0 0]
   [7 5 0]]]


 [[[0 0 0]
   [0 7 0]
   [0 0 8]]

  [[0 0 0]
   [0 4 5]
   [0 0 9]]

  [[4 7 6]
   [0 0 0]
   [0 0 0]]]]
[[[[4 5 0]
   [0 0 2]
   [0 0 0]]

  [[0